## Screen Routines

Subroutines to make an 78 x 25 character screen.

* R7 is return value
* R6 is top of stack
* Subroutine (callee) handles saving/loading of return values and registers


In [27]:
.ORIG x4000
    ;; ------------------------------------------------
    ;; Graphics Routines
    ;; 78 x 25 (25th for special status)
    ;; ------------------------------------------------
    ;; SETUP 
    ;; RESERVED: R6 for stack
    ;;           R7 for RET value
    ;; ------------------------------------------------
            LEA R6, STACK         ;; R6 is Top of STACK
    ;; ------------------------------------------------
            LEA R0, START         ;; GOTO START
            JMP R0                ;; Keep STACK close to reference
STACK:      .BLKW #100            ;; adjust size for your use
START:      JSR DRAWSCREEN        ;; start of actual program
            HALT
    ;; ------------------------------------------------

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; Start of Subroutinues:
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; DRAWSCREEN - draw a 80 x 25 screen
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
DRAWSCREEN: STR R7, R6, #0         ;; Save R7 to Stack
            ADD R6, R6, #1         ;; Increment Stack
            ;;JSR SAVE_REGS
            ;;; ---
            LD R1, OUTPUT1   ;; read OUTPUTS
            LD R2, OUTPUT2   ;; read OUTPUTC
            STR R1, R2, #0   ;; save R1 to R2
            JSR BORDER             ;; draw top border
            AND R2, R2, #0         ;; row count is in R2
ROW:        JSR SCREENROW
            ADD R2, R2, #+1
            LD R3, NEGTWENTYFIVE   ;; -25
            ADD R3, R2, R3
            BRn ROW
            JSR BORDER
            AND R0, R0, #0    ;; terminating \0
            JSR OUTPUT
            LD R0, OUTPUT1   ;; read OUTPUTS
            ;;PUTS
            ;;; ---
            ;;JSR RESTORE_REGS
            ADD R6, R6, #-1        ;; Decrement Stack
            LDR R7, R6, #0         ;; Load Stack into R7
            RET            
OUTPUT1:    .FILL OUTPUTS          ;; store OUTPUTS close
OUTPUT2:    .FILL OUTPUTC          ;; store OUTPUTC close

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; SCREENROW - draws memory row part of screen
;;          - assumes R2 has row count (25, 0)
;;          - uses R0
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
SCREENROW:  STR R7, R6, #0         ;; Save R7 to Stack
            ADD R6, R6, #1         ;; Increment Stack
            ;; stuff here
            LD R0, BAR
            JSR OUTPUT
            ;; screen row memory is in R2 (initially zero)
            ;; multiply row x 78 to get next
            LD R3, SWIDTH
            JSR MULTIPLY           ;; R2 x R3 -> R4
            ;; R4 is now where to start in SCREEN
            ;; start in SCREEN + R4
            ;; show each word, for SWIDTH times
            ADD R5, R3, #0        ;; copy for countdown
            LEA R3, SCREEN         ;; start of memory
            ADD R3, R3, R4        ;; R3 (screen) + R4 (mult)
            LD R1, THIRTYTWO      ;; ASCII space; maps 0 to ...
SRAGAIN:    LDR R0, R3, #0
            ADD R0, R0, R1 
            JSR OUTPUT
            ADD R3, R3, #1
            ADD R5, R5, #-1
            BRp SRAGAIN
            LD R0, BAR
            JSR OUTPUT
            LD R0, NEWLINE
            JSR OUTPUT
            ;; end here
            ADD R6, R6, #-1        ;; Decrement Stack
            LDR R7, R6, #0         ;; Load Stack into R7
            RET            
THIRTYTWO:  .FILL #32

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; BORDER - draw top/bottom border
;;        - uses R0, R1
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
BORDER:     STR R7, R6, #0         ;; Save R7 to Stack
            ADD R6, R6, #1         ;; Increment Stack
            LD R0, PLUS
            JSR OUTPUT
            AND R1, R1, #0         ;; counter
            LD R1, SWIDTH
            LD R0, DASH
SAGAIN:     JSR OUTPUT
            ADD R1, R1, #-1
            BRp SAGAIN
            LD R0, PLUS
            JSR OUTPUT
            LD R0, NEWLINE
            JSR OUTPUT
            ADD R6, R6, #-1        ;; Decrement Stack
            LDR R7, R6, #0         ;; Load Stack into R7
            RET

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; MULTIPLY - multiplies R2 x R3 -> R4
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
MULTIPLY: STR R7, R6, #0         ;; Save R7 to Stack
          ADD R6, R6, #1         ;; Increment Stack 
          ;; ---
          AND R4, R4, #0         ;; total
          AND R5, R5, #0         ;; counter
          ADD R5, R5, R2         ;; set condition codes; R5 is copy of R2
MAGAIN:   BRz DONE               ;; if R5 == 0, done
          ADD R4, R4, R3         ;; 
          ADD R5, R5, #-1        ;; set condition codes
          BR MAGAIN
          ;; --- result is in R4
DONE:     ADD R6, R6, #-1        ;; Decrement Stack
          LDR R7, R6, #0         ;; Load Stack into R7
          RET            

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; OUTPUT - copy R0 to OUTPUTC (current output)
;;        - assumes char in R0
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
OUTPUT:   STR R7, R6, #0         ;; Save R7 to Stack
          ADD R6, R6, #1         ;; Increment Stack 
          ;;JSR SAVE_REGS
          ;; ---
          ;;LDI R4, OUTPUT3        ;; Load OUTPUTC (next char pos)
          ;;STR R0, R4, #0         ;; save R0 char to R1 address
          ;;ADD R4, R4, #1         ;; increment R1
          ;;STI R4, OUTPUT3        ;; Save OUTPUTC
          OUT
          ;; --- 
          ;;JSR RESTORE_REGS
          ADD R6, R6, #-1        ;; Decrement Stack
          LDR R7, R6, #0         ;; Load Stack into R7
          RET            
OUTPUT3:  .FILL OUTPUTC

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; DATA:
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
SWIDTH      .FILL #78  ;; width of screen
PLUS:       .FILL #43  ;; + in ASCII
DASH:       .FILL #45  ;; - in ASCII
BAR:        .FILL #124 ;; | in ASCII
NEWLINE:    .FILL #10  ;; NEWLINE in ASCII
NEGTWENTYFIVE: .FILL #-25
SCREEN:     .BLKW #1950 ;; 78 x 25
OUTPUTC:    .FILL #0
OUTPUTS:    .BLKW #1975 ;; 79 x 25
.END

Assembled! Use %dis or %dump to examine.


## Screen Display

This uses a zero-based display screen where 0 is interpreted to be 0 + 32 = x20 (space in ASCII). See ASCII chart for more characters (0 through 94 are mapped to ASCII 32 through 126). Why? Because no need to attempt to display ASCII 0 through 31, which are control codes).

In [30]:
%mem x40EA x11

Memory disassembled:
           x40EA: x0011 - 17 (or 17)


In [31]:
%mem x40EB x12

Memory disassembled:
           x40EB: x0012 - 18 (or 18)


In [32]:
%mem x4138 x13

Memory disassembled:
           x4138: x0013 - 19 (or 19)


In [33]:
%%time
%exe

+------------------------------------------------------------------------------+
|                                          12                                  |
|                                          3                                   |
|                                                                              |
|                                                                              |
|                                                                              |
|                                                                              |
|                                                                              |
|                                                                              |
|                                                                              |
|                                                                              |
|                                                                              |
|                           

In [34]:
%reset


Welcome to the LC-3 simulator.

The contents of the LC-3 tools distribution, including sources, management
tools, and data, are Copyright (c) 2003 Steven S. Lumetta.

The LC-3 tools distribution is free software covered by the GNU General
Public License, and you are welcome to modify it and/or distribute copies
of it under certain conditions.  The file COPYING (distributed with the
tools) specifies those conditions.  There is absolutely no warranty for
the LC-3 tools distribution, as described in the file NO_WARRANTY (also
distributed with the tools).

Have fun.

Registers:
PC: x3000
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x0000 


In [35]:
.ORIG x4000
.SET MODE TERMINAL
    ;; ------------------------------------------------
    ;; Graphics Routines
    ;; 78 x 25 (25th for special status)
    ;; ------------------------------------------------
    ;; SETUP 
    ;; RESERVED: R6 for stack
    ;;           R7 for RET value
    ;; ------------------------------------------------
            LEA R6, STACK         ;; R6 is Top of STACK
    ;; ------------------------------------------------
            LEA R0, START         ;; GOTO START
            JMP R0                ;; Keep STACK close to reference
STACK:      .BLKW #100            ;; adjust size for your use
START:      JSR DRAWSCREEN        ;; start of actual program
            HALT
    ;; ------------------------------------------------

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; Start of Subroutinues:
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; DRAWSCREEN - draw a 80 x 25 screen
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
DRAWSCREEN: STR R7, R6, #0         ;; Save R7 to Stack
            ADD R6, R6, #1         ;; Increment Stack
            ;;JSR SAVE_REGS
            ;;; ---
            LD R1, OUTPUT1   ;; read OUTPUTS
            LD R2, OUTPUT2   ;; read OUTPUTC
            STR R1, R2, #0   ;; save R1 to R2
            JSR BORDER             ;; draw top border
            AND R2, R2, #0         ;; row count is in R2
ROW:        JSR SCREENROW
            ADD R2, R2, #+1
            LD R3, NEGTWENTYFIVE   ;; -25
            ADD R3, R2, R3
            BRn ROW
            JSR BORDER
            AND R0, R0, #0    ;; terminating \0
            JSR OUTPUT
            LD R0, OUTPUT1   ;; read OUTPUTS
            ;;PUTS
            TERMINAL R0, 0
            TERMINAL R0, 1
            ;;; ---
            ;;JSR RESTORE_REGS
            ADD R6, R6, #-1        ;; Decrement Stack
            LDR R7, R6, #0         ;; Load Stack into R7
            RET            
OUTPUT1:    .FILL OUTPUTS          ;; store OUTPUTS close
OUTPUT2:    .FILL OUTPUTC          ;; store OUTPUTC close

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; SCREENROW - draws memory row part of screen
;;          - assumes R2 has row count (25, 0)
;;          - uses R0
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
SCREENROW:  STR R7, R6, #0         ;; Save R7 to Stack
            ADD R6, R6, #1         ;; Increment Stack
            ;; stuff here
            LD R0, BAR
            JSR OUTPUT
            ;; screen row memory is in R2 (initially zero)
            ;; multiply row x 78 to get next
            LD R3, SWIDTH
            JSR MULTIPLY           ;; R2 x R3 -> R4
            ;; R4 is now where to start in SCREEN
            ;; start in SCREEN + R4
            ;; show each word, for SWIDTH times
            ADD R5, R3, #0        ;; copy for countdown
            LEA R3, SCREEN         ;; start of memory
            ADD R3, R3, R4        ;; R3 (screen) + R4 (mult)
            LD R1, THIRTYTWO      ;; ASCII space; maps 0 to ...
SRAGAIN:    LDR R0, R3, #0
            ADD R0, R0, R1 
            JSR OUTPUT
            ADD R3, R3, #1
            ADD R5, R5, #-1
            BRp SRAGAIN
            LD R0, BAR
            JSR OUTPUT
            LD R0, NEWLINE
            JSR OUTPUT
            ;; end here
            ADD R6, R6, #-1        ;; Decrement Stack
            LDR R7, R6, #0         ;; Load Stack into R7
            RET            
THIRTYTWO:  .FILL #32

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; BORDER - draw top/bottom border
;;        - uses R0, R1
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
BORDER:     STR R7, R6, #0         ;; Save R7 to Stack
            ADD R6, R6, #1         ;; Increment Stack
            LD R0, PLUS
            JSR OUTPUT
            AND R1, R1, #0         ;; counter
            LD R1, SWIDTH
            LD R0, DASH
SAGAIN:     JSR OUTPUT
            ADD R1, R1, #-1
            BRp SAGAIN
            LD R0, PLUS
            JSR OUTPUT
            LD R0, NEWLINE
            JSR OUTPUT
            ADD R6, R6, #-1        ;; Decrement Stack
            LDR R7, R6, #0         ;; Load Stack into R7
            RET

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; MULTIPLY - multiplies R2 x R3 -> R4
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
MULTIPLY: STR R7, R6, #0         ;; Save R7 to Stack
          ADD R6, R6, #1         ;; Increment Stack 
          ;; ---
          AND R4, R4, #0         ;; total
          AND R5, R5, #0         ;; counter
          ADD R5, R5, R2         ;; set condition codes; R5 is copy of R2
MAGAIN:   BRz DONE               ;; if R5 == 0, done
          ADD R4, R4, R3         ;; 
          ADD R5, R5, #-1        ;; set condition codes
          BR MAGAIN
          ;; --- result is in R4
DONE:     ADD R6, R6, #-1        ;; Decrement Stack
          LDR R7, R6, #0         ;; Load Stack into R7
          RET            

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; OUTPUT - copy R0 to OUTPUTC (current output)
;;        - assumes char in R0
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
OUTPUT:   STR R7, R6, #0         ;; Save R7 to Stack
          ADD R6, R6, #1         ;; Increment Stack 
          ;; ---
          LDI R4, OUTPUT3        ;; Load OUTPUTC (next char pos)
          STR R0, R4, #0         ;; save R0 char to R1 address
          ADD R4, R4, #1         ;; increment R1
          STI R4, OUTPUT3        ;; Save OUTPUTC
          ;;OUT
          ;; --- 
          ADD R6, R6, #-1        ;; Decrement Stack
          LDR R7, R6, #0         ;; Load Stack into R7
          RET            
OUTPUT3:  .FILL OUTPUTC

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; DATA:
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
SWIDTH      .FILL #78  ;; width of screen
PLUS:       .FILL #43  ;; + in ASCII
DASH:       .FILL #45  ;; - in ASCII
BAR:        .FILL #124 ;; | in ASCII
NEWLINE:    .FILL #10  ;; NEWLINE in ASCII
NEGTWENTYFIVE: .FILL #-25
SCREEN:     .BLKW #1950 ;; 78 x 25
OUTPUTC:    .FILL #0
OUTPUTS:    .BLKW #1975 ;; 79 x 25
.END

Assembled! Use %dis or %dump to examine.


In [36]:
%%time
%exe

Computation completed
Instructions: 33884
Cycles: 262759 (0.131380 milliseconds)

Registers:
PC: x048E
N: 0 Z: 0 P: 1 
R0: x4864 R1: x0000 R2: x0019 R3: x0000 
R4: x50F0 R5: x0000 R6: x4003 R7: x4069 
Time: 0.4796028137207031 seconds.



In [9]:
%%time
%exe

Computation completed
Instructions: 33884
Cycles: 262759 (0.131380 milliseconds)

Registers:
PC: x048E
N: 0 Z: 0 P: 1 
R0: x4864 R1: x0000 R2: x0019 R3: x0000 
R4: x50F0 R5: x0000 R6: x4003 R7: x4069 
Time: 0.4615483283996582 seconds.



In [10]:
.ORIG x5000
    ;; ------------------------------------------------
            LEA R6, STACK         ;; R6 is Top of STACK
    ;; ------------------------------------------------
            LEA R0, START         ;; GOTO START
            JMP R0                ;; Keep STACK close to reference
STACK:      .BLKW #100            ;; adjust size for your use
START:      LD R2, FIVE
            LD R3, SIX
            JSR MULTIPLY
            HALT
FIVE: .FILL #5
SIX: .FILL #6

;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
;; MULTIPLY - multiplies R2 x R3 -> R4
;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;;
MULTIPLY: STR R7, R6, #0         ;; Save R7 to Stack
          ADD R6, R6, #1         ;; Increment Stack 
          ;;JSR SAVE_REGS
          ;; ---
          AND R4, R4, #0         ;; total
          AND R5, R5, #0         ;; counter
          ADD R5, R5, R2         ;; set condition codes; R5 is copy of R2
MAGAIN:   BRz DONE               ;; if R5 == 0, done
          ADD R4, R4, R3         ;; 
          ADD R5, R5, #-1        ;; set condition codes
          BR MAGAIN
          ;; --- result is in R4
          ;;JSR RESTORE_REGS
DONE:     ADD R6, R6, #-1        ;; Decrement Stack
          LDR R7, R6, #0         ;; Load Stack into R7
          RET            

.END

Assembled! Use %dis or %dump to examine.


In [11]:
%exe

Computation completed
Instructions: 36
Cycles: 235 (0.000117 milliseconds)

Registers:
PC: x048E
N: 0 Z: 0 P: 1 
R0: x5067 R1: x0000 R2: x0005 R3: x0006 
R4: x001E R5: x0000 R6: x5003 R7: x506B 


In [12]:
%reset


Welcome to the LC-3 simulator.

The contents of the LC-3 tools distribution, including sources, management
tools, and data, are Copyright (c) 2003 Steven S. Lumetta.

The LC-3 tools distribution is free software covered by the GNU General
Public License, and you are welcome to modify it and/or distribute copies
of it under certain conditions.  The file COPYING (distributed with the
tools) specifies those conditions.  There is absolutely no warranty for
the LC-3 tools distribution, as described in the file NO_WARRANTY (also
distributed with the tools).

Have fun.

Registers:
PC: x3000
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x0000 
